# Record3D Point Cloud Visualization

This notebook visualizes combined point clouds from all cameras to check alignment.


In [5]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [1]:
!source /workspace/Home_Reconstruction/venv/bin/activate
!pip install --upgrade ipykernel
!/workspace/Home_Reconstruction/venv/bin/python -m ipykernel install --user --name=home_recon_venv --display-name "Python (home_recon_venv)"
!pip install opencv-python
!pip install scikit-image scikit-learn
!pip install ninja


[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip
Installed kernelspec home_recon_venv in /root/.local/share/jupyter/kernels/home_recon_venv

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip

[notice] A new release of pip is available: 24.2 -> 25.3
[notice] To update, run: python -m pip install --upgrade pip


In [2]:
%autoreload 2
import sys
print(sys.executable)

import OpenEXR
from pathlib import Path

PROJECT_ROOT = Path('/workspace/Home_Reconstruction')
sys.path.insert(0, str(PROJECT_ROOT))  # only the parent folder

import scene
from scene.objectgs_model import *
from scene.train import *
from scene.vis_tools.pc_viewer import *

import scene.data_loaders 
from scene.data_loaders.record3d_loader import *
from scene.data_loaders.generate_masks import *

import gsplat

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
%matplotlib inline

/workspace/Home_Reconstruction/venv/bin/python
Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


## Load And View Scene

In [2]:
%autoreload 2
import os
os.environ["PYTORCH_CUDA_ALLOC_CONF"] = "expandable_segments:True"
os.environ['PYTHONIOENCODING'] = 'utf-8'
from scene.data_loaders.generate_masks import *
from huggingface_hub import login
#paste login command w token here
scene_dir = "/workspace/Home_Reconstruction/data_scenes/maria_bedroom"
text_prompts = ["chair","book", "guitar", "bed", "plant", "lamp", "wall", "dresser", "mirror", "shelf", "picture", "postcard", "container", "computer", "clothing", "desk", "record player", "computer"]
n=20

# masks_dir, class_mapping = segment_and_save_incremental(
#     text_prompts=text_prompts,
#     scene_path=scene_dir,
#     save_vis=True,
#     n=(n*4),
#     resume=False,
    
# )

In [3]:
# Step 3: Use the class via the module (no wildcard import)
%autoreload 2
scene_obj = Record3DScene(
    scene_path=scene_dir,
    use_semantics=True,
    subsample=4,
    frame_step=n,
    redo_semantics=False,
)

# Step 4: Check results
print(f"\nSemantic Point Cloud Summary:")
print(f"  Total points: {len(scene_obj.points):,}")
print(f"  Unique objects: {scene_obj.num_objects}")
print(f"  Object IDs: {scene_obj.get_object_ids_list()}")

Loaded metadata from /workspace/Home_Reconstruction/data_scenes/maria_bedroom/EXR_RGBD/metadata.json
  Image dimensions: 720x960
  Number of frames: 9720

Dataset split:
  Training: 486 frames
  Testing:  97 frames

Creating 486 cameras...


Loading cameras: 100%|██████████| 486/486 [00:16<00:00, 30.25it/s]


Created 486 cameras

Creating 97 cameras...


Loading cameras: 100%|██████████| 97/97 [00:02<00:00, 36.44it/s]


Created 97 cameras

Loading point cloud...
Loading semantic point cloud from /workspace/Home_Reconstruction/data_scenes/maria_bedroom/processed_semantic.ply
  Loaded 1,886,852 points with 68 unique objects

Semantic Point Cloud Summary:
  Total points: 1,886,852
  Unique objects: 68
  Object IDs: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67]


In [7]:
%autoreload 2
# Visualize with semantic colors and legend
visualize_pointclouds(
    scene_dir,
    ["processed_semantic.ply"],
    color_by_semantics=True,
    prompts=text_prompts,
)
# # Visualize with semantic colors and legend
# visualize_pointclouds(
#     scene_dir,
#     ["processed_semantic.ply"],
#     color_by_semantics=False,
#     prompts=text_prompts,
# )

✓ Loaded class mapping from class_mapping.json: 89 objects

Loading 1 point cloud(s) from maria_bedroom
🎨 Coloring by SEMANTIC OBJECT ID

Loading processed_semantic.ply...
  ✓ Loaded object IDs: 68 unique objects
      background: 916,500 points
      1: chair: 23,755 points
      2: chair: 744 points
      3: book: 2,069 points
      4: book: 2,095 points
      5: book: 1,303 points
      6: book: 437 points
      7: book: 6,407 points
      8: guitar: 3,088 points
      9: guitar: 62,102 points
      10: bed: 365 points
      11: bed: 592 points
      12: plant: 315 points
      13: plant: 6,368 points
      14: plant: 220,250 points
      15: lamp: 285,974 points
      16: lamp: 83,493 points
      17: wall: 54,286 points
      18: wall: 21,528 points
      19: wall: 3,508 points
      20: wall: 7,417 points
      21: wall: 10,529 points
      22: wall: 38,623 points
      23: wall: 5,816 points
      24: wall: 321 points
      25: dresser: 11,879 points
      26: mirror: 1,384 poin


Summary:
processed_semantic.ply          1,886,852 points (150,000 displayed)

🎨 Object Legend:
----------------------------------------
  background                (72,988 pts)
  1: chair                  (1,931 pts)
  2: chair                  (45 pts)
  3: book                   (143 pts)
  4: book                   (165 pts)
  5: book                   (91 pts)
  6: book                   (33 pts)
  7: book                   (524 pts)
  8: guitar                 (238 pts)
  9: guitar                 (4,971 pts)
  10: bed                   (29 pts)
  11: bed                   (39 pts)
  12: plant                 (29 pts)
  13: plant                 (503 pts)
  14: plant                 (17,300 pts)
  15: lamp                  (22,690 pts)
  16: lamp                  (6,685 pts)
  17: wall                  (4,271 pts)
  18: wall                  (1,692 pts)
  19: wall                  (291 pts)
  20: wall                  (586 pts)
  21: wall                  (823 pts)
  22: wall   

In [11]:
# TRAIN A MODEL FROM SCRATCH
import os
os.environ["PYTHONIOENCODING"] = "utf-8"

import torch
import importlib
import glob
from pathlib import Path

# Reload
import scene.train
import scene.objectgs_model
importlib.reload(scene.train)
importlib.reload(scene.objectgs_model)

from scene.train import GaussianTrainer
from scene.objectgs_model import ObjectGSModel

RESUME_FROM_CHECKPOINT = False
training_run_n = "training_run_2"

model = ObjectGSModel(
    point_cloud=scene_obj.points,
    colors=scene_obj.colors,
    object_ids=scene_obj.object_ids,
    object_names=text_prompts,
    voxel_size=0.02,
    k=10,
).to("cuda")

config = {
    # =================================================================
    # LEARNING RATES  (unchanged — already validated)
    # =================================================================
    "lr": 0.001,
    "lr_feature": 0.0025,
    "lr_position": 0.00016,
    "lr_scaling": 0.005,

    # =================================================================
    # TRAINING DURATION
    # =================================================================
    "num_iterations": 10000,
    "eval_interval": 1000,

    # =================================================================
    # PROGRESSIVE RESOLUTION
    # =================================================================
    "use_progressive_resolution": True,
    "progressive_resolution_schedule": [
        (0.02, 4),
        (0.08, 2),
        (0.90, 1),
    ],

    # =================================================================
    # LOSS WEIGHTS
    # =================================================================
    "lambda_ssim": 0.3,
    "lambda_volume": 0.0001,
    "lambda_scale_reg": 3.0,
    "max_scale": 0.03,
    "lambda_offset_leash": 0.3,
    "adaptive_offset_cap_multiplier": 3.0,

    # =================================================================
    # SEMANTIC LOSS
    # =================================================================
    "use_semantic_loss": True,
    "lambda_semantic": 0.05,
    "semantic_loss_start": 4000,
    "semantic_warmup_iters": 1500,

    # =================================================================
    # DENSIFICATION / PRUNING
    # =================================================================
    "use_densification": True,

    "densify_start": 500,
    "densify_until": 7000,
    "densify_interval": 500,

    "densify_grad_threshold": 3e-5,
    "prune_opacity_threshold": 0.005,

    # NEW — required by updated pruning logic
    "prune_warmup_iters": 2000,     # iteration-based warmup
    "prune_grad_factor": 0.25,      # gradient must be < 0.25 * densify threshold
    "min_cycles": 5,                # sustained low-gradient cycles (500 * 5 = 2500 iters)

    # =================================================================
    # CHECKPOINTING
    # =================================================================
    "checkpoint_topk": 3,
    "checkpoint_metric": "test_l1",
    "lower_is_better": True,
    "progress_render_scale": 0.5,

    # =================================================================
    # EARLY STOPPING
    # =================================================================
    "early_stop_patience_evals": 20,
}




start_iteration = 0
latest_ckpt = None

if RESUME_FROM_CHECKPOINT:
    ckpt_dir = PROJECT_ROOT / "outputs" / "maria_bedroom" / training_run_n / "checkpoints"
    checkpoints = sorted(glob.glob(str(ckpt_dir / "*.pth")))

    if checkpoints:
        latest_ckpt = checkpoints[-1]
        print(f"Loading checkpoint: {latest_ckpt}")
        ckpt = torch.load(latest_ckpt, map_location="cuda")

        # Support both common formats
        if "model_state_dict" in ckpt:
            model.load_state_dict(ckpt["model_state_dict"])
            start_iteration = int(ckpt.get("iteration", 0))
        else:
            model.load_state_dict(ckpt)
            # infer from filename if needed
            stem = Path(latest_ckpt).stem  # checkpoint_010000
            try:
                start_iteration = int(stem.split("_")[-1])
            except Exception:
                start_iteration = 0

        print(f"Resumed from iteration {start_iteration}")
    else:
        print("No checkpoint found, starting fresh")

trainer = GaussianTrainer(
    model=model,
    scene=scene_obj,
    scene_name="maria_bedroom",
    config=config,
    base_output_dir=str(PROJECT_ROOT / "outputs"),
)

trainer.train()
#trainer.export_best_marble(latest_ckpt)


09:20:29 | INFO    | ======================================================================
09:20:29 | INFO    | LOG FILE: /workspace/Home_Reconstruction/outputs/maria_bedroom/training_run_20/training_run_20.log
09:20:29 | INFO    | ======================================================================
09:20:29 | INFO    | Optimizer: Adam with 4 param groups
09:20:29 | INFO    |   features: lr=0.002500 (20475520 params)
09:20:29 | INFO    |   scalings: lr=0.005000 (639860 params)
09:20:29 | INFO    |   offsets: lr=0.000160 (19195800 params)
09:20:29 | INFO    |   mlp: lr=0.001000 (45358 params)
09:20:29 | INFO    | [NN] Computing nearest neighbor distances for 639,860 anchors...


KeyboardInterrupt: 

In [13]:
from time_training import profile

# After creating trainer
profile(trainer, num_iterations=100)

Warming up...
Profiling 100 iterations...

TIMING BREAKDOWN (averaged over 100 iterations)
backward            :   71.87 ±  0.60 ms ( 58.1%)  █████████████████████████████
get_params          :   18.66 ±  0.04 ms ( 15.1%)  ███████
render              :   15.20 ±  0.20 ms ( 12.3%)  ██████
semantic_loss       :   14.09 ±  0.04 ms ( 11.4%)  █████
optimizer_step      :    3.02 ±  0.14 ms (  2.4%)  █
rgb_loss            :    0.79 ±  0.11 ms (  0.6%)  
----------------------------------------------------------------------
TOTAL               :  123.64 ms  (8.1 it/s)

INSIGHTS:
  • Biggest bottleneck: backward (58.1%)
  • Forward: 48.7 ms (39.4%)
  • Backward: 74.9 ms (60.6%)


{'get_params': {'avg_ms': 18.65710536018014,
  'std_ms': 0.03999590431639459,
  'pct': 15.090309468372675},
 'render': {'avg_ms': 15.204297956079245,
  'std_ms': 0.20056797921567884,
  'pct': 12.29759691963098},
 'rgb_loss': {'avg_ms': 0.7928231731057167,
  'std_ms': 0.11278940415269305,
  'pct': 0.64125419270007},
 'semantic_loss': {'avg_ms': 14.088865262456238,
  'std_ms': 0.04084639253205782,
  'pct': 11.395408492596811},
 'backward': {'avg_ms': 71.87385343946517,
  'std_ms': 0.595013258626768,
  'pct': 58.13327791999557},
 'optimizer_step': {'avg_ms': 3.0193884391337633,
  'std_ms': 0.13748070210321617,
  'pct': 2.4421530067038915},
 '_total_ms': 123.63633363042027,
 '_iterations_per_sec': 8.088237257093441}

In [10]:
import torch
import gc



# del model
# del trainer

# Clear Python garbage
gc.collect()

# Clear CUDA cache
torch.cuda.empty_cache()

# Verify
print(f"Allocated: {torch.cuda.memory_allocated() / 1e9:.2f} GB")
print(f"Reserved: {torch.cuda.memory_reserved() / 1e9:.2f} GB")

print(torch.cuda.memory_summary(device='cuda:0', abbreviated=False))

import gc
import torch

tensors = []
for obj in gc.get_objects():
    try:
        if torch.is_tensor(obj) and obj.is_cuda:
            size_mb = obj.element_size() * obj.numel() / 1e6
            tensors.append((size_mb, obj.shape, obj.dtype))
    except:
        pass

print(f"Found {len(tensors)} CUDA tensors")
print(f"Total: {sum(t[0] for t in tensors):.1f} MB")
print()
print("Top 20 largest:")
print("-" * 70)
for size_mb, shape, dtype in tensors[:20]:
    print(f"{size_mb:>10.2f} MB  {str(shape):40s} {dtype}")


Allocated: 5.52 GB
Reserved: 5.88 GB
|===========================================================================|
|                  PyTorch CUDA memory summary, device ID 0                 |
|---------------------------------------------------------------------------|
|            CUDA OOMs: 2            |        cudaMalloc retries: 2         |
|===========================================================================|
|        Metric         | Cur Usage  | Peak Usage | Tot Alloc  | Tot Freed  |
|---------------------------------------------------------------------------|
| Allocated memory      |   5265 MiB |   5649 MiB |  10299 MiB |   5033 MiB |
|       from large pool |   5263 MiB |   5646 MiB |  10289 MiB |   5026 MiB |
|       from small pool |      2 MiB |      3 MiB |      9 MiB |      7 MiB |
|---------------------------------------------------------------------------|
| Active memory         |   5265 MiB |   5649 MiB |  10299 MiB |   5033 MiB |
|       from large pool |  

In [13]:
from pathlib import Path

# ============================================================
# View individual object PLYs from training output
# ============================================================

# # Point to your training run's objects folder
# run_dir = Path("/workspace/Home_Reconstruction/outputs/maria bedroom/training_run_7/final_outputs/objects")

# # List available objects
# print("Available objects:")
# for ply in sorted(run_dir.glob("*.ply")):
#     print(f"  {ply.name}")

# # View a single object by ID
# object_id = 8  # e.g., 1 = nightstand
# ply_file = list(run_dir.glob(f"{object_id:02d}_*.ply"))[0]
# visualize_pointclouds(run_dir, [ply_file.name])



# Point to your training run's objects folder
splat_dir = Path("/workspace/Home_Reconstruction/outputs/maria_bedroom/training_run_3/final_outputs")
ply_name = "splat_supersplat.ply"
visualize_pointclouds(splat_dir, [ply_name])

SyntaxError: invalid syntax (1280567074.py, line 24)

In [ ]:
# ============================================================
# Run the pipeline
# ============================================================
# Comprehensive bedroom prompts
text_prompts = [
    # Main furniture
    "bed",
    "nightstand",
    "dresser",
    "desk",
    "chair",
    "wardrobe",
    "mirror",
    "clothing",
    "jacket",
    "shirt",
    
    # Lighting
    "lamp",
    "ceiling light",
    
    # Textiles
    "pillow",
    "blanket",
    "curtain",
    "rug",
    
    # Structure
    "wall",
    "floor",
    "ceiling",
    "door",
    "window",
    
    # Decor
    "plant",
    "picture frame",
    "book",
    "jewelry",
    "monitor",
    "laptop",
    "jacket",
    "towel",
    "paper",
    "computer",
    "shelf",
    "poster",
    "postcard",
]